

* https://blog.patricktriest.com/analyzing-cryptocurrencies-python/
* https://medium.com/@eliquinox/cryptocurrency-data-analysis-part-i-obtaining-and-playing-with-data-of-digital-assets-2a963a72703b

In [66]:
import os
import numpy as np
import pandas as pd
import pickle
import time
import quandl

# Import plotly and enable offline mode
import plotly.offline as py
import plotly.graph_objs as go
import plotly.figure_factory as ff
py.init_notebook_mode(connected=True)

# Step 1 - Retrive Bitcoin Pricing Data
As its not normally possible to buy altcoins directly, it must be bought through BTC. Lets look at the price

### Step 1.1 - Define Quandl Scraper

In [70]:
def get_quandl_data(quandl_id):
    '''Download and cache Quandl dataseries
    Params:
        quandl_id 
    '''
    cache_path = './data/' + '{}.pkl'.format(quandl_id).replace('/','-')
    try:
        with open(cache_path, 'rb') as f:
            df = pickle.load(f)   
            print('Loaded {} from cache'.format(quandl_id))
    except (OSError, IOError) as err:
        print('Downloading {} from Quandl'.format(quandl_id))
        time.sleep(2) #Be nice and wait a little
        df = quandl.get(quandl_id, returns="pandas")
        df.to_pickle(cache_path)
        print('Cached {} at {}'.format(quandl_id, cache_path))
    return df

### Step 1.2 - Pull data from single exchange

There are multiple bitcoin exchanges, with no single 'true' price. We will get prices from various exchanges, but first lets pull from a single exchange and analyse

In [71]:
usd_btc = get_quandl_data('BCHARTS/KRAKENUSD')
usd_btc.head()

Loaded BCHARTS/KRAKENUSD from cache


Open       High        Low      Close  Volume (BTC)  \
Date                                                                   
2014-01-07  874.67040  892.06753  810.00000  810.00000     15.622378   
2014-01-08  810.00000  899.84281  788.00000  824.98287     19.182756   
2014-01-09  825.56345  870.00000  807.42084  841.86934      8.158335   
2014-01-10  839.99000  857.34056  817.00000  857.33056      8.024510   
2014-01-11  858.20000  918.05471  857.16554  899.84105     18.748285   

            Volume (Currency)  Weighted Price  
Date                                           
2014-01-07       13151.472844      841.835522  
2014-01-08       16097.329584      839.156269  
2014-01-09        6784.249982      831.572913  
2014-01-10        6780.220188      844.938794  
2014-01-11       16698.566929      890.671709

In [72]:
btc_trace = go.Scatter(x=usd_btc.index, y=usd_btc['Weighted Price'])
py.iplot([btc_trace])

### Step 1.3 - Pull in Pricing Data from Different Exchanges

In [73]:
exchanges = ['KRAKEN', 'COINBASE', 'BITSTAMP', 'ITBIT']

exchange_data = {}

for exchange in exchanges:
    exchange_code = 'BCHARTS/{}USD'.format(exchange)
    exchange_data[exchange] = get_quandl_data(exchange_code)

Loaded BCHARTS/KRAKENUSD from cache
Cached BCHARTS/COINBASEUSD at ./data/BCHARTS-COINBASEUSD.pkl
Cached BCHARTS/BITSTAMPUSD at ./data/BCHARTS-BITSTAMPUSD.pkl
Cached BCHARTS/ITBITUSD at ./data/BCHARTS-ITBITUSD.pkl


In [98]:
def merge_dfs_on_column(dfs, col):
    labels = list(dfs.keys())
    df = pd.concat([dfs[l][col] for l in labels], axis=1)
    df.columns = labels
    return df

usd_btc = merge_dfs_on_column(exchange_data, 'Weighted Price')
usd_btc.tail()

KRAKEN     COINBASE     BITSTAMP        ITBIT
Date                                                          
2017-11-16  7434.327022  7568.869960  7562.033954  7559.151838
2017-11-17  7794.534086  7819.782057  7797.297110  7812.800647
2017-11-18  7659.664424  7685.038068  7679.326492  7709.018730
2017-11-19  7848.255061  7922.723223  7863.964169  7926.783972
2017-11-20  7999.998251  8039.112548  8033.351554  8038.800000

### Step 1.4 - Visualise aggregated data

In [96]:
def df_scatter(df, title, seperate_y_axis=False, y_axis_label='', scale='linear', initial_hide=False):
    '''Generate a scatter plot of the entire dataframe'''
    label_arr = list(df)
    series_arr = list(map(lambda col: df[col], label_arr))
    
    layout = go.Layout(
        title=title,
        legend=dict(orientation="h"),
        xaxis=dict(type='date'),
        yaxis=dict(
            title=y_axis_label,
            showticklabels= not seperate_y_axis,
            type=scale
        )
    )
    
    y_axis_config = dict(
        overlaying='y',
        showticklabels=False,
        type=scale )
    
    visibility = 'visible'
    if initial_hide:
        visibility = 'legendonly'
        
    # Form Trace For Each Series
    trace_arr = []
    for index, series in enumerate(series_arr):
        trace = go.Scatter(
            x=series.index, 
            y=series, 
            name=label_arr[index],
            visible=visibility
        )
        
        # Add seperate axis for the series
        if seperate_y_axis:
            trace['yaxis'] = 'y{}'.format(index + 1)
            layout['yaxis{}'.format(index + 1)] = y_axis_config    
        trace_arr.append(trace)

    fig = go.Figure(data=trace_arr, layout=layout)
    py.iplot(fig)

In [99]:
# Plot all of the BTC exchange prices
df_scatter(usd_btc, 'Bitcoin Price (USD) By Exchange')


### 1.4 Clean Aggregated Data

In [100]:
# Remove "0" values
usd_btc.replace(0, np.nan, inplace=True)
df_scatter(usd_btc, 'Bitcoin Price (USD) By Exchange')


In [103]:
# Calculate average BTC price as a new column
usd_btc['Mean'] = usd_btc.mean(axis=1)
df_scatter(usd_btc, 'Bitcoin Price (USD) By Exchange')


In [117]:
# Plot a more recent one
usd_btc_filtered = usd_btc.loc[usd_btc.index > '2017-08-08 08:00:00']

btc_trace = go.Scatter(x=usd_btc_filtered.index, y=usd_btc_filtered['Mean'])
py.iplot([btc_trace])




## Step 2 - Lets start looking at altcoins

### Step 2.1 - Define API Helper function

In [119]:
def get_data(symbol, frequency = 86400):
    '''Download and cache Quandl dataseries
    Params:
        symbol = Currency Pair
        (int) frequency (s) = 300,900,1800,7200,14400,86400 
    '''
    #Params: String symbol, int frequency (s) = 300,900,1800,7200,14400,86400. Defaults to daily
    #Returns: df from first available date
    cache_path = './data/{}_{}.pkl'.format(symbol, frequency)
    try:
        with open(cache_path, 'rb') as f:
            df = pickle.load(f)
            print('Loaded {} from cache'.format(symbol))
    
    except (OSError, IOError) as err:    
      
        
        url ='https://poloniex.com/public?command=returnChartData&currencyPair={}&end=9999999999&period={}&start=0'
        url = url.format(symbol, frequency)
        
        print('Downloading {} from {}'.format(symbol, url))
        
        time.sleep(1) #Lets not hammer the api, max 6 calls a second
        df = pd.read_json(url)

        df.set_index('date',inplace=True)
    
        df.to_pickle(cache_path)
        print('Downloaded and cached {} at {}'.format(symbol, cache_path))
    return df

### Step 2.2 - Download altcoin data 

In [53]:
# Load Altcoin data
altcoins = ['OMG', 'XMR', 'VTC', 'LTC', 'GAS']

# coins not on api = 'NEO', 'OMG', 'WTC', 'BNB', 'DNT', 'AEON',
altcoin_data = {}
for altcoin in altcoins:
    coinpair = 'BTC_{}'.format(altcoin)

    altcoin_data[altcoin] = get_data(coinpair)
    
    

Loaded BTC_OMG from cache
Loaded BTC_XMR from cache
Loaded BTC_VTC from cache
Loaded BTC_LTC from cache
Loaded BTC_GAS from cache


In [122]:
altcoin_data['OMG'].tail()

close      high       low      open    quoteVolume      volume  \
date                                                                            
2017-11-16  0.000913  0.001071  0.000904  0.001056  144857.727594  142.396401   
2017-11-17  0.000992  0.001014  0.000890  0.000908  145891.075964  138.454319   
2017-11-18  0.001030  0.001134  0.000975  0.000991  267218.041900  280.006332   
2017-11-19  0.000968  0.001073  0.000932  0.001029  123777.582406  125.158032   
2017-11-20  0.000990  0.001002  0.000949  0.000972  137150.240147  135.716572   

            weightedAverage  
date                         
2017-11-16         0.000983  
2017-11-17         0.000949  
2017-11-18         0.001048  
2017-11-19         0.001011  
2017-11-20         0.000990

### Step 2.3 Aggregate Data onto a single dataframe

In [132]:
#Lets calculate the USD price for each altcoin
for altcoin in altcoin_data.keys():
    altcoin_data[altcoin]['price_usd'] =  altcoin_data[altcoin]['weightedAverage'] * usd_btc['Mean']

altcoin_data['OMG'].tail()

close      high       low      open    quoteVolume      volume  \
date                                                                            
2017-11-16  0.000913  0.001071  0.000904  0.001056  144857.727594  142.396401   
2017-11-17  0.000992  0.001014  0.000890  0.000908  145891.075964  138.454319   
2017-11-18  0.001030  0.001134  0.000975  0.000991  267218.041900  280.006332   
2017-11-19  0.000968  0.001073  0.000932  0.001029  123777.582406  125.158032   
2017-11-20  0.000990  0.001002  0.000949  0.000972  137150.240147  135.716572   

            weightedAverage  price_usd  
date                                    
2017-11-16         0.000983   7.403067  
2017-11-17         0.000949   7.408148  
2017-11-18         0.001048   8.050906  
2017-11-19         0.001011   7.978410  
2017-11-20         0.000990   7.943845

In [133]:
# Merge the USD price onto a single dataframe
df_altcoin = merge_dfs_on_column(altcoin_data, 'price_usd')
df_altcoin.tail()

OMG         XMR       VTC        LTC        GAS
date                                                            
2017-11-16  7.403067  121.010173  4.312531  65.404780  19.452820
2017-11-17  7.408148  122.780718  4.199684  67.717635  23.771380
2017-11-18  8.050906  129.167312  4.296557  67.247212  28.900436
2017-11-19  7.978410  130.378572  4.209624  70.644454  24.488507
2017-11-20  7.943845  133.931660  4.111125  71.202389  23.545824

In [136]:
#Add BTC price to dataframe
df_altcoin['BTC'] = usd_btc['Mean']
df_altcoin.tail()

OMG         XMR       VTC        LTC        GAS          BTC
date                                                                         
2017-11-16  7.403067  121.010173  4.312531  65.404780  19.452820  7531.095694
2017-11-17  7.408148  122.780718  4.199684  67.717635  23.771380  7806.103475
2017-11-18  8.050906  129.167312  4.296557  67.247212  28.900436  7683.261928
2017-11-19  7.978410  130.378572  4.209624  70.644454  24.488507  7890.431606
2017-11-20  7.943845  133.931660  4.111125  71.202389  23.545824  8027.815588

In [137]:
df_scatter(df_altcoin, 'Cryptocurrency Prices (USD)', seperate_y_axis=False, y_axis_label='Coin Value (USD)', scale='log')

Not very useful... Deceptive its on a log scale. Lets try to index the data and look at a more recent timeperiod

In [151]:
index_date = '2017-09-14' #Gas only starts here
df_altcoin_filtered = df_altcoin.loc[df_altcoin.index > index_date]
df_scatter(df_altcoin_filtered, 'Cryptocurrency Prices (USD)', seperate_y_axis=False, y_axis_label='Coin Value (USD)', scale='log')

In [147]:
df_altcoin.loc[index_date]

OMG            NaN
XMR      51.564337
VTC       0.543095
LTC      46.697246
GAS            NaN
BTC    3420.206767
Name: 2017-08-08 00:00:00, dtype: float64

In [153]:
df_altcoin_norm = df_altcoin_filtered.divide(df_altcoin.loc[index_date]) * 100
df_scatter(df_altcoin_norm, 'Cryptocurrency Prices (USD)', seperate_y_axis=False, y_axis_label='Coin Value (USD)')

Looks like everything has underperformed BTC, expect for VTC

## Step 3 - Lets look at correlations

For some reason correlation matrix should be done on percentage changes for stationary statitics. Don't quite understand, but for now i copy!

In [157]:
# Convert to percentage change matrix
df_altcoin_filtered
df_altcoin_pct = df_altcoin_filtered.pct_change()
df_altcoin_pct.tail()

OMG       XMR       VTC       LTC       GAS       BTC
date                                                                  
2017-11-16 -0.042684  0.004207  0.015459  0.030071  0.007665  0.067364
2017-11-17  0.000686  0.014631 -0.026167  0.035362  0.222002  0.036516
2017-11-18  0.086764  0.052016  0.023067 -0.006947  0.215766 -0.015737
2017-11-19 -0.009005  0.009377 -0.020233  0.050519 -0.152660  0.026964
2017-11-20 -0.004332  0.027252 -0.023399  0.007898 -0.038495  0.017411

In [158]:
def correlation_heatmap(df, title, absolute_bounds=True):
    '''Plot a correlation heatmap for the entire dataframe'''
    heatmap = go.Heatmap(
        z=df.corr(method='pearson').as_matrix(),
        x=df.columns,
        y=df.columns,
        colorbar=dict(title='Pearson Coefficient'),
    )
    
    layout = go.Layout(title=title)
    
    if absolute_bounds:
        heatmap['zmax'] = 1.0
        heatmap['zmin'] = -1.0
        
    fig = go.Figure(data=[heatmap], layout=layout)
    py.iplot(fig)

In [159]:
correlation_heatmap(df_altcoin_pct.pct_change(), "Cryptocurrency Correlations since {}".format(index_date))

Highest correlation between LTC and BTC at -0.25. No strong positve correlations

In [163]:
### Lets look at some scatter plots between the most correlated pairs

In [164]:
#Correlation BTC AND LTC
tc_trace = go.Scatter(x=df_altcoin_pct['BTC'], y=df_altcoin_pct['LTC'], mode='markers')
py.iplot([btc_trace])

In [165]:
#Correlation BTC AND VTC

btc_trace = go.Scatter(x=df_altcoin_pct['BTC'], y=df_altcoin_pct['VTC'], mode='markers')
py.iplot([btc_trace])